In [1]:
import spacy

# check if model is available
spacy_model_name = "de_core_news_lg"
if not spacy.util.is_package(spacy_model_name):
    spacy.cli.download(spacy_model_name)
nlp = spacy.load(spacy_model_name)

In [2]:
import json
import pandas as pd
import aki_prj23_transparenzregister.utils.mongo.connector as conn
from aki_prj23_transparenzregister.config.config_providers import JsonFileConfigProvider
import aki_prj23_transparenzregister.utils.mongo.news_mongo_service as news
import aki_prj23_transparenzregister.utils.mongo.ner_service

In [3]:
# Mongo Connect: create connection string and connect
config_provider = JsonFileConfigProvider("../../secrets.json")
engine = config_provider.get_mongo_connection_string()
connector = conn.MongoConnector(config_provider.get_mongo_connection_string())

In [7]:
# Read data from database
newsObj = news.MongoNewsService(connector)
allNews = newsObj.get_all()

# Create a cursor which has all unprogressed articles; articles without the attribute 'companies'
CursorUnprogressed = newsObj.collection.find({"companies": {"$exists": False}})
documents = list(CursorUnprogressed)

In [8]:
# load company list
with open("CompEntities.json", "rb") as fp:
    company_list = json.load(fp)

In [9]:
# documents.rewind()
entity = "ORG"  # "PERSON" LOC
docAttrib = "text"  # "title"

if len(documents) > 0:
    for document in documents:
        # ents=NERService.NERCompanyList(company_list,document)
        ents = NERService.NERSpacy(document, entity, docAttrib)

        # if ents != []:
        print(ents)
        # add a new attribute 'companies' to document
        # newsObj.collection.update_one(
        #        {"_id": document["_id"]},  # Filter für das entsprechende Dokument
        #        {"$set": {"companies": ents}}  # Neues Attribut hinzufügen, initialisiert mit einer leeren Liste
        #    )

else:
    print("No documents found.")

{'US-Notenbank': 1, 'US-Arbeitsministerium': 1, 'US-Verbraucherpreisen': 1, 'Ford': 1, 'US-Inflationsdaten': 1, 'Federal Reserve': 1, 'US-Teuerung': 1, 'Fed': 5, 'Leitzinskorridor': 1, 'Repräsentantenhaus': 1, 'Vanguard Europe': 1, 'US-Geldpolitik': 2, 'EZB': 2, 'US-Aktienmarkt': 1, 'US-Rezession': 1, 'FAQ': 1}
{'Federal Reserve': 2, 'Fed': 7, 'US-Teuerungsrate': 1, 'Nasdaq': 3, 'Dow Jones': 1, 'UBS-Analyst': 1, 'US-Inflation': 1, 'US-Notenbank': 3, 'EZB': 2, 'Bank of Japan': 1, 'Europäischen Zentralbank': 1, 'Europäische Zentralbank': 1, 'Bank von England': 1, 'Markets.com': 1, "People's Bank of China": 1, 'PBoC': 1, 'Adidas': 1, 'Zalando': 1, 'Oracle': 1, 'Volkswagen': 2, 'VW': 1, 'Skoda': 1, 'Seat': 1, 'Siemens': 2, 'Digital Industries': 1, 'Silver Lake': 1, 'Darmstädter Software AG': 1, 'US-Beteiligungsgesellschaft': 1, 'US-Handelsaufsicht': 1, 'Videospielanbieters Activision Blizzard': 1, 'Microsoft': 1, 'FTC': 2}
{'Ticketverkäufers': 1, 'TV-Satiriker': 1, 'TV-Satirikers': 1, 'ZDF

In [19]:
CursorProgressed = newsObj.collection.find({"companies": {"$exists": True}})

In [20]:
docs = list(CursorProgressed)

In [21]:
docs

[{'_id': 'f6f64332-a721-43b2-a6e1-0d64be343712',
  'title': 'Bezahlen mit der Karte - bald ohne Maestro',
  'date': '2023-06-17T07:14:11.918+02:00',
  'text': ' Das Maestro-Logo gehörte bislang normalerweise zur Girocard, der früheren EC-Karte. Nun wird Maestro nach und nach aufs internationale Zahlungssystem von Mastercard und Visa umgestellt. Was dabei zu beachten ist.   Manche Kunden deutscher Banken und Sparkassen sind verunsichert. Denn ab dem 1. Juli wird das gewohnte Maestro-Logo bei vielen neuen Girokarten - den ehemaligen EC-Karten - nicht mehr auf der Vorderseite prangen. Keinen Grund zur Aufregung sieht Oliver Hommel von Euro Kartensysteme in Frankfurt, dem Gemeinschaftsunternehmen der deutschen Banken und Sparkassen, das sich um die Einsatzmöglichkeiten der Girocard in ganz Europa kümmert: "Die bestehenden Karten bleiben bis zum Ablaufdatum gültig und können auch weiterhin eingesetzt werden."  Noch nie funktionierte die deutsche Girocard im Ausland: Sie war und ist auf eine